In [ ]:
import altair as alt
import bulum.io as oio
import folium
from branca.element import Template, MacroElement
import pandas as pd
import numpy as np

## <span style='color:midnightblue'> Map 1 - map with plot in icon </span>

<div class="alert alert-block alert-success">
The map below shows how to add a marker with a plot in the pop up.
</div>

In [2]:
df = oio.read_ts_csv(".\Plot4\GB_Daily_00a_Hist_SKD.csv")
newdf=df.reset_index()
newdf=newdf.rename(columns={'Storage\\0013 Storm King Dam\Storage Volume (ML)':'Storm King Dam Storage Volume (ML)'})

alt.data_transformers.disable_max_rows()

skdChart = alt.Chart(newdf).mark_line().encode(
        alt.X('Date:T'),
        alt.Y('Storm King Dam Storage Volume (ML):Q',
          axis=alt.Axis(title='Storage volume (ML)'))
).properties(width=600,height=300,title="Storm King Dam Dam modelled storage volume").interactive()

##########################
# Map of storage results #
##########################

m = folium.Map(location=[-28.71,151.99], zoom_start=10, tiles="Stamen Terrain")

model_subareas=r".\Map1\SADD_ModelSubareas.geojson" 

model_subareas_style = lambda x: {'color':'#b12ef7'}

folium.GeoJson(model_subareas,name="geojson",style_function=model_subareas_style).add_to(m)

skdPopup=folium.Popup(max_width=700).add_child(folium.features.VegaLite(skdChart,height=350,width=700))

folium.Marker([-28.709,151.993],popup=skdPopup,tooltip="Storm King Dam",icon=folium.Icon(icon="line-chart",prefix='fa',color='darkblue')).add_to(m)

m

## <span style='color:midnightblue'> Map 2 - map with info in tooltips and legend </span>

<div class="alert alert-block alert-success">
The map below shows how to add markers with lots of info in the tooltip and a legend.
</div>

In [3]:
result_path='.\Plot3'

results_files=['BR_RCP85_2050_00a_TexasTWS.in_stats.csv',
               'BR_RCP85_2050_00a_YelarbonTWS.in_stats.csv',
               'BR_RCP85_2050_00a_GoondiwindiTWS.in_stats.csv',
               'BR_RCP85_2050_00a_InglewoodTWS.in_stats.csv',
               'GB_RCP85_2050_00a_StanthorpeTWS.in_stats.csv',
               'GB_RCP85_2050_00a_UnallocHS.in_stats.csv',
               'UB_RCP85_2050_00a_YarramanTWS.in_stats.csv',
               'UB_RCP85_2050_00a_ToowoombaTWS.in_stats.csv',
               'MC_RCP85_2050_00a_ChinchillaTWS.in_stats.csv']

users=['Texas TWS',  'Yelarbon TWS', 'Goondiwindi TWS', 'Inglewood TWS', 'Stanthorpe TWS', 'Unallocated HP', 'Yarraman TWS', 'Toowoomba TWS', 'Chinchilla TWS']

catchment=['Border Rivers', 'Border Rivers', 'Border Rivers', 'Border Rivers', 'Granite Belt', 'Granite Belt', 'Upper Brisbane', 'Upper Brisbane', 'Middle Condamine']

demand=[270, 106, 1800, 488, 1150, 1500, 200, 24000, 1165]

results=[]

for file in results_files:
    results.append(pd.read_csv(result_path + '\\' + file))

def rating_hist(x):
    if x >= 1:
        return 'Good'
    elif x > 0.9:
        return 'OK'
    elif x > 0.8:
        return 'Poor'
    elif x > 0.5:
        return 'Very Poor'
    else:
        return 'Extremely Poor'

def cc_trend(x):
    if x >= 10:
        return 'Strongly positive'
    elif x >= 7:
        return 'Positive'
    elif x >= 5:
        return 'Neutral'
    elif x >= 3:
        return 'Negative'
    else:
        return 'Strongly negative'

def cc_sensi(x):
    if x >= 0.5:
        return 'Extreme'
    elif x >= 0.25:
        return 'Very high'
    elif x >= 0.15:
        return 'High'
    elif x >= 0.05:
        return 'Moderate'
    else:
        return 'Low'

hist_results=[]
hist_rating=[]
gcm_results=[]

for result in results:
    hist_results.append(result.loc[0,'Annual reliability'])
    hist_rating.append(rating_hist(result.loc[0,'Annual reliability']))
    gcm_results.append(result.loc[1:11,'Annual reliability'])

gcm_maint=[]
gcm_reduc=[]
rat_trend=[]
gcm_10th=[]
gcm_90th=[]
rat_sensi=[]
i=0

for result in gcm_results:
    gcm_maint.append(np.count_nonzero(result >= hist_results[i]))
    gcm_reduc.append(np.count_nonzero(result < hist_results[i]))
    rat_trend.append(cc_trend(gcm_maint[i]))
    gcm_10th.append(np.percentile(result,10))
    gcm_90th.append(np.percentile(result,90))
    rat_sensi.append(cc_sensi(hist_results[i] - gcm_10th[i]))
    i+=1

# This generates the legend
template = """
{% macro html(this, kwargs) %}

<!doctype html>
<html lang="en">
<head>
  <meta charset="utf-8">
  <meta name="viewport" content="width=device-width, initial-scale=1">
  <title>jQuery UI Draggable - Default functionality</title>
  <link rel="stylesheet" href="//code.jquery.com/ui/1.12.1/themes/base/jquery-ui.css">

  <script src="https://code.jquery.com/jquery-1.12.4.js"></script>
  <script src="https://code.jquery.com/ui/1.12.1/jquery-ui.js"></script>
  
  <script>
  $( function() {
    $( "#maplegend" ).draggable({
                    start: function (event, ui) {
                        $(this).css({
                            right: "auto",
                            top: "auto",
                            bottom: "auto"
                        });
                    }
                });
});

  </script>
</head>
<body>

 
<div id='maplegend' class='maplegend' 
    style='position: absolute; z-index:9999; border:2px solid grey; background-color:rgba(255, 255, 255, 0.8);
     border-radius:6px; padding: 10px; font-size:14px; right: 20px; bottom: 20px;'>
     
<div class='legend-title'>Historical performance rating</div>
<div class='legend-scale'>
  <ul class='legend-labels'>
    <li><span style='background:#009FEF;opacity:0.7;'></span>Good</li>
    <li><span style='background:#57B956;opacity:0.7;'></span>OK</li>
    <li><span style='background:#FFEBCD;opacity:0.7;'></span>Poor</li>
    <li><span style='background:#FFA500;opacity:0.7;'></span>Very poor</li>
    <li><span style='background:darkred;opacity:0.7;'></span>Extremely poor</li>

  </ul>
</div>
</div>
 
</body>
</html>

<style type='text/css'>
  .maplegend .legend-title {
    text-align: left;
    margin-bottom: 5px;
    font-weight: bold;
    font-size: 90%;
    }
  .maplegend .legend-scale ul {
    margin: 0;
    margin-bottom: 5px;
    padding: 0;
    float: left;
    list-style: none;
    }
  .maplegend .legend-scale ul li {
    font-size: 80%;
    list-style: none;
    margin-left: 0;
    line-height: 18px;
    margin-bottom: 2px;
    }
  .maplegend ul.legend-labels li span {
    display: block;
    float: left;
    height: 16px;
    width: 30px;
    margin-right: 5px;
    margin-left: 0;
    border: 1px solid #999;
    }
  .maplegend .legend-source {
    font-size: 80%;
    color: #777;
    clear: both;
    }
  .maplegend a {
    color: #777;
    }
</style>
{% endmacro %}"""

histPerfRatLeg = MacroElement()
histPerfRatLeg._template = Template(template)

#This generates the map and then adds the legend
m = folium.Map(location=[-27.92,151.00], zoom_start=8, tiles="Stamen Terrain")

sadd_outline=r".\Map2\SADD_RWAArea.geojson" 

sadd_outline_style = lambda x: {'color':'#000000'}

folium.GeoJson(sadd_outline,name="geojson",style_function=sadd_outline_style).add_to(m)

def marker_colour(v):
    if v == 'Extremely Poor' or v == 'Strongly negative' or v == 'Extreme':
        return 'darkred'
    elif v== 'Very Poor' or v == 'Negative' or v == 'Very high':
        return 'orange'
    elif v== 'Poor' or v == 'Neutral' or v == 'High':
        return 'beige'
    elif v== 'OK' or v == 'Positive' or v == 'Moderate':
        return 'green'
    elif v== 'Good' or v == 'Strongly positive' or v == 'Low':
        return 'blue'

tooltips=[
"<b>User:</b> " + users[0] + "<br><b>Model subarea:</b> " + catchment[0] + "<br><b>Reliability:</b> " + "{:,.1%}".format(hist_results[0]) + " (" + hist_rating[0] + ")<br><b>CC trend rating:</b> " + rat_trend[0] + "<br><b>CC sensitivity rating:</b> " + rat_sensi[0],
"<b>User:</b> " + users[1] + "<br><b>Model subarea:</b> " + catchment[1] + "<br><b>Reliability:</b> " + "{:,.1%}".format(hist_results[1]) + " (" + hist_rating[1] + ")<br><b>CC trend rating:</b> " + rat_trend[1] + "<br><b>CC sensitivity rating:</b> " + rat_sensi[1],
"<b>User:</b> " + users[2] + "<br><b>Model subarea:</b> " + catchment[2] + "<br><b>Reliability:</b> " + "{:,.1%}".format(hist_results[2]) + " (" + hist_rating[2] + ")<br><b>CC trend rating:</b> " + rat_trend[2] + "<br><b>CC sensitivity rating:</b> " + rat_sensi[2],
"<b>User:</b> " + users[3] + "<br><b>Model subarea:</b> " + catchment[3] + "<br><b>Reliability:</b> " + "{:,.1%}".format(hist_results[3]) + " (" + hist_rating[3] + ")<br><b>CC trend rating:</b> " + rat_trend[3] + "<br><b>CC sensitivity rating:</b> " + rat_sensi[3],
"<b>User:</b> " + users[4] + "<br><b>Model subarea:</b> " + catchment[4] + "<br><b>Reliability:</b> " + "{:,.1%}".format(hist_results[4]) + " (" + hist_rating[4] + ")<br><b>CC trend rating:</b> " + rat_trend[4] + "<br><b>CC sensitivity rating:</b> " + rat_sensi[4],
"<b>User:</b> " + users[5] + "<br><b>Model subarea:</b> " + catchment[5] + "<br><b>Reliability:</b> " + "{:,.1%}".format(hist_results[5]) + " (" + hist_rating[5] + ")<br><b>CC trend rating:</b> " + rat_trend[5] + "<br><b>CC sensitivity rating:</b> " + rat_sensi[5],
"<b>User:</b> " + users[6] + "<br><b>Model subarea:</b> " + catchment[6] + "<br><b>Reliability:</b> " + "{:,.1%}".format(hist_results[6]) + " (" + hist_rating[6] + ")<br><b>CC trend rating:</b> " + rat_trend[6] + "<br><b>CC sensitivity rating:</b> " + rat_sensi[6],
"<b>User:</b> " + users[7] + "<br><b>Model subarea:</b> " + catchment[7] + "<br><b>Reliability:</b> " + "{:,.1%}".format(hist_results[7]) + " (" + hist_rating[7] + ")<br><b>CC trend rating:</b> " + rat_trend[7] + "<br><b>CC sensitivity rating:</b> " + rat_sensi[7],
"<b>User:</b> " + users[8] + "<br><b>Model subarea:</b> " + catchment[8] + "<br><b>Reliability:</b> " + "{:,.1%}".format(hist_results[8]) + " (" + hist_rating[8] + ")<br><b>CC trend rating:</b> " + rat_trend[8] + "<br><b>CC sensitivity rating:</b> " + rat_sensi[8]]

folium.Marker([-28.855,151.168],tooltip=tooltips[0],icon=folium.Icon(icon='home',prefix='fa',color=marker_colour(hist_rating[0]))).add_to(m)
folium.Marker([-28.572,150.753],tooltip=tooltips[1],icon=folium.Icon(icon='home',prefix='fa',color=marker_colour(hist_rating[1]))).add_to(m)
folium.Marker([-28.542,150.301],tooltip=tooltips[2],icon=folium.Icon(icon='home',prefix='fa',color=marker_colour(hist_rating[2]))).add_to(m)
folium.Marker([-28.415,151.082],tooltip=tooltips[3],icon=folium.Icon(icon='home',prefix='fa',color=marker_colour(hist_rating[3]))).add_to(m)
folium.Marker([-28.655,151.934],tooltip=tooltips[4],icon=folium.Icon(icon='home',prefix='fa',color=marker_colour(hist_rating[4]))).add_to(m)
folium.Marker([-28.803,151.850],tooltip=tooltips[5],icon=folium.Icon(icon='circle-o',prefix='fa',color=marker_colour(hist_rating[5]))).add_to(m)
folium.Marker([-26.841,151.981],tooltip=tooltips[6],icon=folium.Icon(icon='home',prefix='fa',color=marker_colour(hist_rating[6]))).add_to(m)
folium.Marker([-27.560,151.951],tooltip=tooltips[7],icon=folium.Icon(icon='home',prefix='fa',color=marker_colour(hist_rating[7]))).add_to(m)
folium.Marker([-26.767,150.758],tooltip=tooltips[8],icon=folium.Icon(icon='home',prefix='fa',color=marker_colour(hist_rating[8]))).add_to(m)

m.get_root().add_child(histPerfRatLeg)

m